In [1]:
import os
from nltk.stem import PorterStemmer
import math


allfiles_tokens = [] # a list of doc of tokens
vocabulary = dict() # all unrepaeat tokens
sorted_vocabulary = [] 


# tokenize

path = './IRTM/'
filenames = os.listdir(path)
for file in filenames:
    fp = open(f'{path}{file}', 'r')    
    singlefile_tokens = []
    for line in fp:
        modified_line = []
        for i in line:
            if i.isalpha() or i == ' ':
                modified_line.append(i)
        modified_line = ''.join(modified_line)

        singleline_tokens = modified_line.split(' ')
        for token in singleline_tokens:
            if token:
                singlefile_tokens.append(token)
    fp.close()

    for i in range(len(singlefile_tokens)):
        singlefile_tokens[i] = singlefile_tokens[i].lower()

    ps = PorterStemmer()
    for i in range(len(singlefile_tokens)):
        singlefile_tokens[i] = ps.stem(singlefile_tokens[i])

    singlefile_results = []
    nltk_stopwords = ['news', 'im', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', "you're", "you've", "you'll", "you'd", 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', 'she', "she's", 'her', 'hers', 'herself', 'it', "it's", 'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', "that'll", 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'have', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more', 'most', 'other', 'some', 'such', 'no', 'nor', 'not', 'only', 'own', 'same', 'so', 'than', 'too', 'very', 's', 't', 'can', 'will', 'just', 'don', "don't", 'should', "should've", 'now', 'd', 'll', 'm', 'o', 're', 've', 'y', 'ain', 'aren', "aren't", 'couldn', "couldn't", 'didn', "didn't", 'doesn', "doesn't", 'hadn', "hadn't", 'hasn', "hasn't", 'haven', "haven't", 'isn', "isn't", 'ma', 'mightn', "mightn't", 'mustn', "mustn't", 'needn', "needn't", 'shan', "shan't", 'shouldn', "shouldn't", 'wasn', "wasn't", 'weren', "weren't", 'won', "won't", 'wouldn', "wouldn't"]
    nltk_stopwords = set(nltk_stopwords)
    for i in range(len(singlefile_tokens)):
        if singlefile_tokens[i] not in nltk_stopwords:
            singlefile_results.append(singlefile_tokens[i])
    
    allfiles_tokens.append(singlefile_results)

    
# save in dictionary

allfiles_tokens_set = [None] * len(allfiles_tokens) # a list of doc of unrepeat tokens

for i, document in enumerate(allfiles_tokens):
    allfiles_tokens_set[i] = set(document)
    for token in allfiles_tokens_set[i]:
        if token in vocabulary:
            vocabulary[token] += 1
        else:
            vocabulary[token] = 1



# sort the dictionary

for token in vocabulary:
    sorted_vocabulary.append(token)
sorted_vocabulary.sort()



In [10]:
number_of_class = 13
training_set = [None] * number_of_class
count_docs = 0

fp = open('training.txt', 'r')
for line in fp:
    words = line.strip().split(' ')
    class_name = int(words[0])
    training_set[class_name-1] = []
    for i in range(1, len(words)):
        training_set[class_name-1].append(words[i])
        count_docs += 1
fp.close()


In [127]:
from collections import Counter
import heapq

prior_each_class = [0] * number_of_class
count_docs_each_class = [0] * number_of_class
tokens_each_class = [None] * number_of_class
count_tokens_each_class = [0] * number_of_class
count_token_freq = dict()
selected_token = []

# count prior

for i in range(number_of_class):
    for document in training_set[i]:
        count_docs_each_class[i] += 1
for i in range(number_of_class):
    prior_each_class[i] = count_docs_each_class[i] / count_docs

    
# count all tokens in each class

for i in range(number_of_class):
    tokens_each_class[i] = []
    for document in training_set[i]:
        for token in allfiles_tokens[int(document)]:
            tokens_each_class[i].append(token)
            

# count numbers of all tokens in each class
            
for i in range(number_of_class):
    count_tokens_each_class[i] = len(tokens_each_class[i])


# count each token frequency in each class
    
for word in vocabulary:
    count_token_freq[word] = []
    for class_name in range(number_of_class):
        count_token_freq[word].append(Counter(tokens_each_class[class_name])[word])

# count Likelihood Ratios in each class
        
for class_c in range(number_of_class):
    likelihood_tokens = dict()
    top_k_tokens = []
    for token in tokens_each_class[class_c]:
        n_11 = count_token_freq[token][class_c] # present and on topic
        n_01 = sum(count_token_freq[token]) - n_11  # present and off topic
        n_10 = count_tokens_each_class[class_c] - n_11 # absent and on topic
        n_00 = sum(count_tokens_each_class) - sum(count_token_freq[token]) - n_10 # absent and off topic
        N = sum(count_tokens_each_class)
        
        a = (((n_11+n_01)/N)**n_11) * ((1-(n_11+n_01)/N)**n_10) * (((n_11+n_01)/N)**n_01) * ((1-(n_11+n_01)/N)**n_00)
        b = ((n_11/(n_11+n_10))**n_11) * ((1-n_11/(n_11+n_10))**n_10) * ((n_01/(n_01+n_00))**n_01) * ((1-n_01/(n_01+n_00))**n_00)
        if a!=0 and b != 0:
            x = -2 * math.log(a/b)
        else:
            x = 0
        likelihood_tokens[token] = x
        
    y = heapq.nlargest(38, likelihood_tokens.items(), key=itemgetter(1))
    top_k_tokens = list(map(itemgetter(0), y))
    
    for token in top_k_tokens:
        selected_token.append(token)
        



In [146]:
selected_vocabulary = set()
selected_tokens_each_class = [None] * number_of_class
count_selected_tokens_each_class = [None] * number_of_class
count_selected_token_freq = dict()
selected_vocabulary = set(selected_token)
condProb = dict()

for i in range(number_of_class):
    selected_tokens_each_class[i] = []
    for token in tokens_each_class[i]:
        if token in selected_vocabulary:
            selected_tokens_each_class[i].append(token)
    count_selected_tokens_each_class[i] = len(selected_tokens_each_class[i])
    
for token in selected_vocabulary:
    condProb[token] = []
    for i in range(number_of_class):
        condProb[token].append(Counter(selected_tokens_each_class[i])[token])       
       





In [169]:
total_training = []

for i in range(number_of_class):
    for document in training_set[i]:
        total_training.append(int(document))
        
total_training = sorted(total_training)

for document in range(1, len(allfiles_tokens)+1):
    if document not in total_training:
        
        print(document)
    








17
18
20
21
22
23
24
25
26
27
28
30
32
33
34
35
36
37
38
39
40
41
42
43
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
71
72
73
74
75
76
77
78
79
80
81
82
84
85
87
88
89
90
91
93
94
95
96
97
98
99
101
103
104
105
106
107
108
109
110
111
112
114
116
117
118
119
120
121
122
123
124
125
126
127
128
129
144
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
242
246
247
249
251
252
253
257
259
261
263
264
265
266
267
268
269
270
271
272
273
274
276
277
280
281
282
283
284
285
286
287
288
289
290
291
292
293
294
297
298
299
300
302
303
306
307
310
311
312
313
314
318
319
322
323
329
330
331
332
333
334
335
336
339
340
342
343
344
345
346
347
348
349

In [77]:
# save file
savefilename = 'tokens_each_class_1.txt'  
rp = open(savefilename, 'w')
for token in tokens_each_class[1]:
    rp.write(f'{token}\n')

rp.close()

In [170]:
allfiles_tokens

[['white',
  'hous',
  'also',
  'keep',
  'close',
  'watch',
  'yugoslavia',
  'opposit',
  'forc',
  'step',
  'pressur',
  'presid',
  'slobodan',
  'milosev',
  'work',
  'nbc',
  'jim',
  'maceda',
  'belgrad',
  'tonight',
  'serbia',
  'eve',
  'gener',
  'strike',
  'thi',
  'twohour',
  'roadblock',
  'tast',
  'come',
  'tomorrow',
  'say',
  'opposit',
  'nationwid',
  'work',
  'stoppag',
  'begin',
  'purpos',
  'forc',
  'man',
  'say',
  'stole',
  'presidenti',
  'elect',
  'slobodan',
  'milosev',
  'peopl',
  'dont',
  'accept',
  'victim',
  'hostag',
  'one',
  'person',
  'milosev',
  'time',
  'work',
  'pressur',
  'work',
  'four',
  'year',
  'ago',
  'hundr',
  'thousand',
  'serb',
  'march',
  'milosev',
  'call',
  'gener',
  'strike',
  'well',
  'protest',
  'last',
  'three',
  'month',
  'milosev',
  'surviv',
  'real',
  'question',
  'doe',
  'opposit',
  'power',
  'confront',
  'regim',
  'combin',
  'wealth',
  'get',
  'rid',
  'case',
  'point',

In [166]:
len(allfiles_tokens)

1095

In [154]:
condProb['bank']

[1, 0, 9, 1, 1, 7, 0, 0, 5, 1, 2, 0, 2]

In [155]:
training_set

[['11',
  '19',
  '29',
  '113',
  '115',
  '169',
  '278',
  '301',
  '316',
  '317',
  '321',
  '324',
  '325',
  '338',
  '341'],
 ['1',
  '2',
  '3',
  '4',
  '5',
  '6',
  '7',
  '8',
  '9',
  '10',
  '12',
  '13',
  '14',
  '15',
  '16'],
 ['813',
  '817',
  '818',
  '819',
  '820',
  '821',
  '822',
  '824',
  '825',
  '826',
  '828',
  '829',
  '830',
  '832',
  '833'],
 ['635',
  '680',
  '683',
  '702',
  '704',
  '705',
  '706',
  '708',
  '709',
  '719',
  '720',
  '722',
  '723',
  '724',
  '726'],
 ['646',
  '751',
  '781',
  '794',
  '798',
  '799',
  '801',
  '812',
  '815',
  '823',
  '831',
  '839',
  '840',
  '841',
  '842'],
 ['995',
  '998',
  '999',
  '1003',
  '1005',
  '1006',
  '1007',
  '1009',
  '1011',
  '1012',
  '1013',
  '1014',
  '1015',
  '1016',
  '1019'],
 ['700',
  '730',
  '731',
  '732',
  '733',
  '735',
  '740',
  '744',
  '752',
  '754',
  '755',
  '756',
  '757',
  '759',
  '760'],
 ['262',
  '296',
  '304',
  '308',
  '337',
  '397',
  '401',
